In [ ]:
# Importando as bibliotecas.
import pandas as pd
import numpy as np
import folium
from folium import plugins

In [ ]:
# lendo arquivo do site Brasil.IO
file = pd.read_csv('drive/My Drive/caso_full-2.csv',sep=',')

In [ ]:
# Colunas do arquivo
file.head(1)

city  city_ibge_code        date  ...  state  new_confirmed  new_deaths
0  São Paulo       3550308.0  2020-02-25  ...     SP              1           0

[1 rows x 17 columns]

In [ ]:
# Lendo arquivo Cidades_brasileiras.csv
municipios = pd.read_csv('drive/My Drive/Cidades_brasileiras.csv',sep=';')

In [ ]:
# Colunas do arquivo
municipios.head(1)

codigo_ibge             nome  latitude  ...  capital  codigo_uf  Unnamed: 6
0      5200050  Abadia de Goiás  -16.7573  ...        0         52         NaN

[1 rows x 7 columns]

In [ ]:
# Indexando o arquivo pelo código IBGE
municipios = municipios.set_index('codigo_ibge')

In [ ]:
municipios.head(1)

nome  latitude  ...  codigo_uf  Unnamed: 6
codigo_ibge                             ...                       
5200050      Abadia de Goiás  -16.7573  ...         52         NaN

[1 rows x 6 columns]

In [ ]:
# Criar a matriz cities
cities = file.loc[file.place_type =='city' , : ]
cities.place_type.unique()

array(['city'], dtype=object)

In [ ]:
# Unindo os arquivos pelo código IBGE
cities = cities.join(municipios, on='city_ibge_code')
cities.head(1)

city  city_ibge_code        date  ...  capital  codigo_uf  Unnamed: 6
0  São Paulo       3550308.0  2020-02-25  ...      1.0       35.0         NaN

[1 rows x 23 columns]

In [ ]:
# Criar o arquivo geo_last
geo_last = cities.loc[cities.is_last==True, ['city', 'latitude', 'longitude', 'state', 'last_available_confirmed', 'last_available_deaths']]

In [ ]:
geo_last.head(1)

city  ...  last_available_deaths
226265  Importados/Indefinidos  ...                      0

[1 rows x 6 columns]

In [ ]:
# Verificando a quantidade de Municípios em geo_last
len(geo_last)

5418

In [ ]:
# Verificando a quantidade de casos confirmados na coluna last_available_confirmed.
geo_last.last_available_confirmed.sum()

2151754

In [ ]:
# Verificando a quantidade de óbitos.
geo_last.last_available_deaths.sum()

80775

In [ ]:
# Verificando a quantidade de Estados no arquivo geo_last
len(geo_last.state.unique())

27

In [ ]:
# Criando um mapa base do território brasileiro.
baseMap = folium.Map(
    width= "100%",
    height="100%",
    location=[-15.788497, -47.879873],
    zoom_start=4
)
      

In [ ]:
baseMap

In [ ]:
# Eliminando valores nulos no arquivo geo_last
geo_last = geo_last.dropna()


In [ ]:
geo_last.head(1)

city  latitude  ...  last_available_confirmed last_available_deaths
351154  Acorizal   -15.194  ...                        60                     1

[1 rows x 6 columns]

In [ ]:
geo_last.iloc[0]['latitude']

-15.194

In [ ]:
geo_last.iloc[0]['longitude']

-56.3632

In [ ]:
# Linhas e Colunas do arquivo
geo_last.shape

(5400, 6)

In [ ]:
# Adicionando "CIDADE", "ESTADO", "CASOS", "MORTES" no mapa
for i in range(0, len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'] , geo_last.iloc[i]['longitude']],
        color = 'RED', #00FF69
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: ' +str(geo_last.iloc[i]['city']) +
                  '<li><bold> ESTADO: ' +str(geo_last.iloc[i]['state']) +
                  '<li><bold> CASOS:  ' +str(geo_last.iloc[i]['last_available_confirmed']) +
                  '<li><bold> MORTES: ' +str(geo_last.iloc[i]['last_available_deaths']),
        radius = (geo_last.iloc[i]['last_available_confirmed']** 0.5) 
    ).add_to(baseMap)

In [ ]:
baseMap

In [ ]:
baseMap.save('cidades.html')